# Loading Packages necessary for simulation

In [1]:
using Pkg;
Pkg.instantiate();
cd(@__DIR__);
using PowerDynamics;
using Plots;
using DataFrames;
using OrdinaryDiffEq: ODEProblem, Rodas4, solve;
include("plotting.jl");
include("helpers.jl");
include("simulate_pd.jl");

  Updating registry at `~/.julia/registries/General`
  Updating git-repo `https://github.com/JuliaRegistries/General.git`
Fetching: [========================================>]  100.0 %.0 %

# Model Building

In [5]:
node_list=[
    CurtailedPowerPlantWithInertia(P=0.5,ω_0=2π*50,T_AI=20,K_PPLL=50,K_IPLL=625,T_d=0.003,T_f=0.004,K_PV=0.28,K_IV=186),
    SlackAlgebraic(U=1), #node 2
    CurtailedPowerPlantWithInertia(P=2.5,ω_0=2π*50,T_AI=20,K_PPLL=50,K_IPLL=625,T_d=0.003,T_f=0.004,K_PV=0.28,K_IV=186),
    PQAlgebraic(P=-0.478, Q=-0.0), #node 4
    PQAlgebraic(P=-0.076, Q=-0.016), #node 5
    SwingEqLVS(H=5.06, P=-0.112, D=0.0063662, Ω=314.159, Γ=2, V=1), #node 6
    PQAlgebraic(P=-0.0, Q=-0.0), #node 7
    SwingEqLVS(H=10.06, P=0.0, D=0.0063662, Ω=314.159, Γ=2, V=1), #node 8
    PQAlgebraic(P=-0.295,Q= -0.166), #node 9
    PQAlgebraic(P=-0.09, Q=-0.058), #node 10
    PQAlgebraic(P=-0.035,Q= -0.018), #node 11
    PQAlgebraic(P=-0.061, Q=-0.016), #node 12
    PQAlgebraic(P=-0.135, Q=-0.058), #node 13
    PQAlgebraic(P=-0.149, Q=-0.05) #node 14
];

line_list=[
    PiModelLine(from=1, to=2, y=4.99913-15.2631im, y_shunt_km=1/2*0.0528*1im, y_shunt_mk=1/2*0.0528*1im), # line 1
    PiModelLine(from=1, to=5, y=1.0259-4.23498im, y_shunt_km=1/2*0.0492*1im, y_shunt_mk=1/2*0.0492*1im),  # line 2
    PiModelLine(from=2, to=3, y=1.13502-4.78186im, y_shunt_km=1/2*0.0438*1im, y_shunt_mk=1/2*0.0438*1im), # line 3
    PiModelLine(from=2, to=4, y=1.68603-5.11584im, y_shunt_km=1/2*0.0374*1im, y_shunt_mk=1/2*0.0374*1im), # line 4
    PiModelLine(from=2, to=5, y=1.70114-5.19393im, y_shunt_km=1/2*0.034*1im, y_shunt_mk=1/2*0.034*1im), # line 5
    PiModelLine(from=3, to=4, y=1.98598-5.06882im, y_shunt_km=1/2*0.0346*1im, y_shunt_mk=1/2*0.0346*1im), # line 6
    PiModelLine(from=4, to=5, y=6.84098-21.5786im, y_shunt_km=1/2*0.0128*1im, y_shunt_mk=1/2*0.0128*1im), # line 7
    PiModelLine(from=4, to=7, y=0.0-4.78194im, y_shunt_km=0,y_shunt_mk=0), # line 8
    PiModelLine(from=4, to=9, y=0.0-1.79798im, y_shunt_km=0,y_shunt_mk=0), # line 9
    PiModelLine(from=5, to=6, y=0.0-3.96794im, y_shunt_km=0,y_shunt_mk=0), # line 10
    PiModelLine(from=6, to=11,y=1.95503-4.09407im, y_shunt_km=0,y_shunt_mk=0), # line 11
    PiModelLine(from=6, to=12, y=1.52597-3.17596im, y_shunt_km=0,y_shunt_mk=0), # line 12
    PiModelLine(from=6, to=13, y=3.09893-6.10276im, y_shunt_km=0,y_shunt_mk=0), # line 13
    PiModelLine(from=7, to=8, y=0.0-5.67698im, y_shunt_km=0,y_shunt_mk=0), # line 14
    PiModelLine(from=7, to=9, y=0.0-9.09008im, y_shunt_km=0,y_shunt_mk=0), # line 15
    PiModelLine(from=9, to=10, y=3.90205-10.3654im, y_shunt_km=0,y_shunt_mk=0), # line 16
    PiModelLine(from=9, to=14, y=1.42401-3.02905im, y_shunt_km=0,y_shunt_mk=0), # line 17
    PiModelLine(from=10, to=11,y= 1.88088-4.40294im, y_shunt_km=0,y_shunt_mk=0), # line 18
    PiModelLine(from=12, to=13, y=2.48902-2.25197im, y_shunt_km=0,y_shunt_mk=0), # line 19
    PiModelLine(from=13, to=14, y=1.13699-2.31496im, y_shunt_km=0,y_shunt_mk=0) # line 20
];

powergrid = PowerGrid(node_list,line_list)
operationpoint = find_operationpoint(powergrid);

## Line tripping

In [6]:
disturbed_nodes=[12,13]
simulation_time=(0.,5.)

sol_lf,result_lf,faulty_grid= simulate_linefault(disturbed_nodes,powergrid,operationpoint,simulation_time);
plot_res(result_lf,faulty_grid,disturbed_nodes[1]);

In [7]:
determine_rocof_nadir(faulty_grid,sol_lf,simulation_time[2])

4×3 DataFrame
│ Row │ node  │ RoCoF     │ nadir      │
│     │ Int64 │ Float64   │ Float64    │
├─────┼───────┼───────────┼────────────┤
│ 1   │ 6     │ 0.0369169 │ 0.00303759 │
│ 2   │ 8     │ 0.0098124 │ 0.00092629 │
│ 3   │ 1     │ 0.0386104 │ 6.54379e-6 │
│ 4   │ 3     │ 0.0757343 │ 1.44437e-5 │

## Sudden Loss of Load

In [8]:
timespan= (0.,5);
disturbed_node=4;

pd = PowerPerturbation(node_number=disturbed_node,fraction=0.5, tspan_fault=(0.5,5));
sol_pd,result_pd = simulate_pd(pd,powergrid,operationpoint,timespan)

plot_res(result_pd,powergrid,disturbed_node)

In [9]:
# RoCoF and nadir for the base power grid with a line fault
include("helpers.jl");
determine_rocof_nadir(powergrid,sol_pd,timespan[2])

4×3 DataFrame
│ Row │ node  │ RoCoF     │ nadir      │
│     │ Int64 │ Float64   │ Float64    │
├─────┼───────┼───────────┼────────────┤
│ 1   │ 6     │ 1.74252   │ 0.112035   │
│ 2   │ 8     │ 1.13286   │ 0.0983555  │
│ 3   │ 1     │ 0.0200999 │ 0.00374263 │
│ 4   │ 3     │ 0.0500225 │ 0.00622263 │